In [1]:
import os
import pandas as pd

# Path to the directory containing the CSV files
directory_path = '/data1-8tb-blk/sp2023stock/Insight-Wave/TopicModeling/result/integrationOutput/id/thairath_ids.csv'

articles_list = {}

df = pd.read_csv(directory_path)
articles_list = df['ID'].tolist()

print(f'max = {max(articles_list)}, min = {min(articles_list)}')


max = 2753122, min =2365221


In [2]:
import os

main = os.getcwd()
dataset_thairath = main + '/../../../data/thairath/article/'

start_process = main +  '/../../../src/Parsing/thairath/parsing_progress.txt'
end_process = main + '/../../../src/Crawling/thairath/progress.txt'

In [3]:
import os
import re
import pandas as pd
import chardet
from bs4 import BeautifulSoup

# Detect input file
def htmlInput(file_path):
    with open(file_path, "r", encoding='utf-8') as file:
        html_content = file.read()
    soup = BeautifulSoup(html_content, "html.parser")
    return soup

#Extract title
def extract_title(soup):
    title = soup.title.string.strip() if soup.title else None
    return title

#Extract body
def extract_body(soup):
    article_divs = soup.find_all("div", itemprop="articleBody")
    articles = []
    if article_divs:
        for inside_div in article_divs:
            articleses = inside_div.find_all('p')
            for article in articleses:
                articles.append(article.get_text(strip=True))
    return articles

#Extract tags
def extract_tags(soup):
    tags_div = soup.find("div", class_="__item_article-breadcrumb css-7obyzk e1wlf1s66")
    tag_content = [tag.get_text(strip=True) for tag in tags_div.find_all('a')] if tags_div else None
    return tag_content

#Extract date
def extract_pubdate(soup):
    month_list = {'ม.ค.': '01', 'ก.พ.': '02', 'มี.ค.': '03', 'เม.ย.': '04', 'พ.ค.': '05', 'มิ.ย.': '06', 'ก.ค.': '07', 'ส.ค.': '08', 'ก.ย.': '09', 'ต.ค.': '10', 'พ.ย.': '11', 'ธ.ค.': '12'}
    date_time_div = soup.find('div', {'class': '__item_article-date css-1v3en5e e1wlf1s65'})
    
    datestamps = ""
    timestamps = ""
    year = ""
    numMonth = ""
    date = ""

    if date_time_div is not None:
        date_time_string = date_time_div.get_text(strip=True)
        datestamps = " ".join(date_time_string.split())
        timestamps = " ".join(date_time_string.split()[3:4])

        for month_dict in month_list:
            if month_dict in datestamps:
                month = month_dict
                numMonth = month_list[str(month)]
                date = " ".join(date_time_string.split()[:1])
                year = " ".join(date_time_string.split()[2:3])

        if year != "":
            year = str(int(year) - 543)
        datestamps = year + "-" + numMonth + "-" + date
        pubdate = datestamps + " " + timestamps
    else:
        pubdate = None

    return pubdate

#Extract title
def extract_intro(soup):
    intro_div = soup.find("div", class_="css-1wn93q2 evs3ejl67")
    intro = ""
    if intro_div:
        intro = intro_div.get_text(strip=True)
    else:
        intro = None
    
    return intro

def extract_urlPic(soup):
    # Try to find the primary image first
    primary_div = soup.find('div', class_="container")
    if primary_div:
        primary_img = primary_div.find('img')
        if primary_img:
            primary_src = primary_img.get('src')
            # Check if the src length is less than 40
            if len(primary_src) >= 40:
                return primary_src
            else:
                # If the primary src is too short, look for the alternative
                alternative_div = soup.find('div', class_="css-a1g4gz e1xtbsxb1")
                if alternative_div:
                    alternative_img = alternative_div.find('img')
                    if alternative_img:
                        alternative_src = alternative_img.get('src')
                        return alternative_src
                    else:
                        print("No alternative img tag found.")
                        return None
                else:
                    print("No alternative div with class 'css-a1g4gz e1xtbsxb1' found.")
                    return None
        else:
            print("No img tag found inside the primary div.")
            return None
    else:
        print("No primary div with class 'container' found.")
        return None


# #Start
# if os.path.exists(start_process):
#     with open('parsing_progress.txt','r') as f:
#         progress_start = int(f.readline().strip())
#         start_id = progress_start - 1
# else: 
#     print("Start path doesn't exists process start from 1")
#     start_id = 1 
    
# article_id = start_id

# #End
# if os.path.exists(end_process):
#     with open(process,'r') as f:
#         progress_end = int(f.readline().strip())
#         end_id = progress_end + 1
# else: 
#     print("End path doesn't exists")
# print(f'Start parsing at {start_id} and Ending at {end_id}' )


print(f'Start parsing process')
for article_id in articles_list: #range(start_id, end_id+1):

    print(f'Processing article id {article_id}')
    file_path = dataset_thairath + str(article_id) + "/index.txt"
    
    if os.path.exists(file_path):
        print("Index TXT Processing ID: " + str(article_id))
        
        soup = htmlInput(file_path)
        title = extract_title(soup)
        intro = extract_intro(soup)
        articles = extract_body(soup)
        pubdate = extract_pubdate(soup)
        tag_content = extract_tags(soup)
        url = extract_urlPic(soup)
        
        data_dict = {'Title': title, 'Intro': intro, 'Article': articles, 'DateTime': pubdate, 'Tags': tag_content, 'url_picture': url}
        
        output_path = dataset_thairath + str(article_id) + "/parsing.txt"
        with open(os.path.join(output_path), 'w', encoding="utf-8") as f:
            for key, value in data_dict.items():
                if value is not None:
                    if key == 'Tags' and isinstance(value, list):
                        f.write(f"[::{key}::]\n")
                        for tags in value:
                            f.write(f"{tags}\n")
                            
                    elif key == 'Article' and isinstance(value, list):
                        f.write(f"[::{key}::]\n")
                        for bodys in value:
                            if bodys == 'SPONSORED':
                                continue
                            else:
                                f.write(f"{bodys}\n")
                                f.write("\n")
                    else:
                        f.write(f"[::{key}::]\n{value}\n")


# Write the last processed article_id to 'csv_progress.txt' after loop ends
with open('csv_progress.txt', 'w') as f:
    f.write(str(article_id) + '\n')

Start parsing process
Processing article id 2753122
Index TXT Processing ID: 2753122
No alternative img tag found.
Processing article id 2752718
Index TXT Processing ID: 2752718
No alternative div with class 'css-a1g4gz e1xtbsxb1' found.
Processing article id 2752646
Index TXT Processing ID: 2752646
Processing article id 2752291
Index TXT Processing ID: 2752291
No alternative img tag found.
Processing article id 2751859
Index TXT Processing ID: 2751859
Processing article id 2751853
Index TXT Processing ID: 2751853
No alternative div with class 'css-a1g4gz e1xtbsxb1' found.
Processing article id 2751848
Index TXT Processing ID: 2751848
No alternative div with class 'css-a1g4gz e1xtbsxb1' found.
Processing article id 2751846
Index TXT Processing ID: 2751846
Processing article id 2751845
Index TXT Processing ID: 2751845
Processing article id 2751844
Index TXT Processing ID: 2751844
Processing article id 2751843
Index TXT Processing ID: 2751843
Processing article id 2751842
Index TXT Proce